In [6]:
# Function to load ARFF file into a list of dictionaries
def load_arff(file_path):
    with open(file_path, 'r') as f:
        lines = f.readlines()
    data_start = lines.index('@data\n') + 1
    attributes = [line.split()[1] for line in lines if line.startswith('@attribute')]
    data_list = []

    for line in lines[data_start:]:
        values = line.strip().split(',')
        data_dict = {attr: val if val != 'm' else None for attr, val in zip(attributes, values)}
        data_list.append(data_dict)

    return data_list

def preprocess_data(data_list):
    for entry in data_list:
        for key, value in entry.items():
            if value == 'm':
                entry[key] = None

    return data_list

def linear_interpolation(data_list):
    for i in range(1, len(data_list) - 1):
        for key, value in data_list[i].items():
            if value is None and data_list[i - 1][key] is not None and data_list[i + 1][key] is not None:
                data_list[i][key] = (float(data_list[i - 1][key]) + float(data_list[i + 1][key])) / 2

    return data_list

def z_score_standardization(matrix):
    for i in range(2, len(matrix[0])):
        column = [float(row[i]) for row in matrix if row[i] is not None and row[i] != 'm']

        if len(set(column)) == 1:
            continue

        mean_val = sum(column) / len(column)

        if len(column) > 1:
            std_dev = (sum((x - mean_val) ** 2 for x in column) / len(column)) ** 0.5
        else:
            std_dev = 0

        for row in matrix:
            if row[i] is not None and row[i] != 'm':
                if std_dev != 0:
                    row[i] = (float(row[i]) - mean_val) / std_dev
                else:
                    row[i] = 0  

    return matrix

def dot_product(v1, v2):
    result = sum(x * y for x, y in zip(v1, v2) if isinstance(x, (int, float)) and isinstance(y, (int, float)))
    return result

def subtract(v1, v2):
    return [x - y for x, y in zip(v1, v2)]

def scale(vector, scalar):
    return [x * scalar for x in vector]

def multiply_matrix_vector(matrix, vector):
    return [dot_product(row, vector) for row in matrix]

def multiply_matrix(matrix1, matrix2):
    result = []
    for row in matrix1:
        new_row = []
        for col in transpose(matrix2):
            element = dot_product(row, col)
            new_row.append(element)
        result.append(new_row)
    return result

def transpose(matrix):
    return [[row[i] for row in matrix] for i in range(len(matrix[0]))]

def mean(column):
    values = [float(val) for val in column if val is not None]
    return sum(values) / len(values) if values else 0

def covariance_matrix(matrix):
    n = len(matrix)
    num_features = len(matrix[0])
    transposed_matrix = transpose(matrix)
    cov_matrix = [[0] * num_features for _ in range(num_features)]

    for i in range(num_features):
        for j in range(num_features):
            mean_i = mean(matrix[i])
            mean_j = mean(matrix[j])
            values_i = [float(val) for val in matrix[i] if val is not None]
            values_j = [float(val) for val in matrix[j] if val is not None]
            cov_matrix[i][j] = sum((val_i - mean_i) * (val_j - mean_j) for val_i, val_j in zip(values_i, values_j)) / (n - 1)

    return cov_matrix

def custom_random():
    seed = 1
    while True:
        seed = (seed * 1103515245 + 12345) & 0x7FFFFFFF
        yield seed / 0x7FFFFFFF


# Function to perform PCA
def pca(data_matrix, num_components):
    # Calculate the covariance matrix
    cov_matrix = covariance_matrix(data_matrix)

    # Calculate the eigenvalues and eigenvectors using power iteration
    num_features = len(data_matrix[0])
    eigenvalues = [0] * num_features
    eigenvectors = [[0] * num_features for _ in range(num_features)]

    random_generator = custom_random()

    for i in range(num_features):
        # Use a simple random number generator as the initial approximation
        vector = [next(random_generator) for _ in range(num_features)]

        for _ in range(1000):  # Adjust the number of iterations as needed
            new_vector = multiply_matrix_vector(cov_matrix, vector)
            magnitude = sum(x ** 2 for x in new_vector) ** 0.5
            vector = scale(new_vector, 1 / magnitude)

        eigenvalues[i] = dot_product(new_vector, vector)
        eigenvectors[i] = vector

    # Sort eigenvalues and corresponding eigenvectors in descending order
    sorted_indices = sorted(range(num_features), key=lambda k: eigenvalues[k], reverse=True)
    eigenvalues = [eigenvalues[i] for i in sorted_indices]
    eigenvectors = [[eigenvectors[j][i] for j in sorted_indices] for i in range(num_features)]

    # Select the top 'num_components' eigenvectors
    top_eigenvectors = eigenvectors[:num_components]

    # Project the data onto the new subspace defined by the top eigenvectors
    pca_result = multiply_matrix(data_matrix, transpose(top_eigenvectors))

    return pca_result



def display_data_table(data_list):
    # Get the attribute names
    attributes = list(data_list[0].keys())

    # Calculate the maximum width for each column
    column_widths = {attr: max(len(attr), max(len(str(entry[attr])) for entry in data_list)) for attr in attributes}

    # Print header
    header = "|".join(f"{attr:^{column_widths[attr]}}" for attr in attributes)
    print(header)
    print("-" * sum(column_widths.values()))

    # Print data rows
    for entry in data_list:
        row = "|".join(f"{str(entry[attr]):^{column_widths[attr]}}" if entry[attr] is not None else 'm' for attr in attributes)
        print(row)


def display_matrix(matrix):
    for row in matrix:
        formatted_row = "|".join(f"{float(cell):^14.4f}" if cell is not None and cell != 'm' else 'm' for cell in row)
        print(formatted_row)


# load and preprocess data for each year
file_path_2017 = r'.\dataset\2017.arff' 
file_path_2018 = r'.\dataset\2018.arff'
file_path_2019 = r'.\dataset\2019.arff'
file_path_2020 = r'.\dataset\2020.arff'
file_path_2021 = r'.\dataset\2021 Q1.arff'

data_2017 = load_arff(file_path_2017)
data_2018 = load_arff(file_path_2018)
data_2019 = load_arff(file_path_2019)
data_2020 = load_arff(file_path_2020)
data_2021 = load_arff(file_path_2021)

data_2017_preprocessed = preprocess_data(data_2017)
data_2018_preprocessed = preprocess_data(data_2018)
data_2019_preprocessed = preprocess_data(data_2019)
data_2020_preprocessed = preprocess_data(data_2020)
data_2021_preprocessed = preprocess_data(data_2021)

# perform linear interpolation for each year
data_2017_preprocessed = linear_interpolation(data_2017_preprocessed)
data_2018_preprocessed = linear_interpolation(data_2018_preprocessed)
data_2019_preprocessed = linear_interpolation(data_2019_preprocessed)
data_2020_preprocessed = linear_interpolation(data_2020_preprocessed)
data_2021_preprocessed = linear_interpolation(data_2021_preprocessed)


# Combine data from all quarters
data_combined = data_2017_preprocessed + data_2018_preprocessed + data_2019_preprocessed + data_2020_preprocessed + data_2021_preprocessed
print(type(data_combined))


# Extract attributes
attributes = list(data_combined[0].keys())

# Initialize a list to represent the matrix
matrix = []

# matrix conversion
for entry in data_combined:
    row = [entry[attr] for attr in attributes[2:]] # excludes 'year' and 'quarter' attributes
    matrix.append(row)

# display_matrix(matrix)

# perform data standardization before doing PCA & SVD 
standardized_data = z_score_standardization(matrix)
display_matrix(standardized_data)

num_components = 2  # Set the desired number of principal components
pca_result = pca(standardized_data, num_components) # perform PCA

print("\n\nPCA Result:")
display_matrix(pca_result)

<class 'list'>
    0.1400    |    0.5300    |    0.0033    |   -0.0625    |   -0.0209    |    0.0227    |   -0.0694    |   -0.0215    |   -0.0215    |    0.0227    |    0.0221    |    0.0212    |    0.0709    |    0.0217    |   -0.0673    |    0.0224    |    0.0234    |    0.0227    |    0.0088    |   -0.0215    |    0.0085    |   -0.0280    |    0.0105    |    1.3848    |   -0.0309    |   -0.0339    |   -0.0248    |   -0.0220    |   -0.5009    |   -0.0215    |   -0.0799    |   -0.0215    |   -0.8151    |   -0.0132    |    0.0275    |    0.0510    |   -0.0453    |   -0.0212    |    0.0242    |   -0.0508    |   -0.0227    |    0.0119    |    0.0110    |    2.1530    |   -0.0278    |   -0.0781    |    0.1673    |    0.3745    |   -0.0613    |   -0.0588    |    0.0242    |m|m|   -0.0209    |    0.0006    |    0.0208    |   -0.0099    |    0.0207    |m|   -0.0403    |   -0.0412    |m|m|m|m|   -0.0290    |   -0.0448    |   -0.0538    |   -0.0354    |   -0.0215    |   -0.1269    |   -0.0249 

The output took 2 minutes and more depending on the computer. This code is designed to handle the analysis of time-series data stored in ARFF files. It begins by loading the data for each year from 2017 to 2021 using the `load_arff` function, which parses the files and organizes the information into a list of dictionaries. The data then undergoes preprocessing, where missing values are denoted by 'm' and transformed into `None` for consistency. Subsequently, linear interpolation is applied to fill in the gaps in the dataset by averaging adjacent data points.

The script proceeds to combine the preprocessed data from all quarters into a single dataset, denoted as `data_combined`. Following this, the code converts the dataset into a matrix format, excluding the 'year' and 'quarter' attributes. Z-score standardization is then performed on the matrix, ensuring that each attribute has a mean of 0 and a standard deviation of 1.

The code leverages a set of linear algebra operations such as dot product, matrix multiplication, and transposition, providing the foundational tools for subsequent analyses. The main analytical focus of the code is Principal Component Analysis (PCA). The `pca` function computes the principal components of the standardized data using a simplified power iteration method. It calculates the covariance matrix, extracts eigenvalues and eigenvectors, sorts them, and selects the top eigenvectors based on the specified number of components.

Finally, the standardized data and the results of the PCA are displayed using utility functions. The former is presented in a matrix format, and the latter showcases the reduced-dimensional representation of the data, capturing its most significant patterns. In essence, this code forms a comprehensive pipeline for processing and analyzing time-series data, offering functionalities ranging from data loading and preprocessing to advanced techniques like PCA.

In [8]:
import numpy as np
from sklearn.decomposition import PCA
from sklearn.decomposition import TruncatedSVD
from sklearn.preprocessing import StandardScaler
from sklearn.impute import SimpleImputer

def load_arff(file_path):
    with open(file_path, 'r') as f:
        lines = f.readlines()

    # Find the start of data
    data_start = lines.index('@data\n') + 1

    # Get attribute names
    attributes = [line.split()[1] for line in lines if line.startswith('@attribute')]

    # Initialize an empty list to store dictionaries
    data_list = []

    # Parse the data and convert it into dictionaries
    for line in lines[data_start:]:
        values = line.strip().split(',')
        data_dict = {attr: val if val != 'm' else None for attr, val in zip(attributes, values)}
        data_list.append(data_dict)

    return data_list


def preprocess_data(data_list):
    for entry in data_list:
        for key, value in entry.items():
            if value == 'm':
                entry[key] = None

    return data_list

def linear_interpolation(data_list):
    for i in range(1, len(data_list) - 1):
        for key, value in data_list[i].items():
            if value is None and data_list[i - 1][key] is not None and data_list[i + 1][key] is not None:
                # Convert string to numeric type before performing division
                data_list[i][key] = (float(data_list[i - 1][key]) + float(data_list[i + 1][key])) / 2

    return data_list

def z_score_standardization(matrix):
    for i in range(2, len(matrix[0])):
        # Extract non-None and non-'m' values
        column = [float(row[i]) for row in matrix if row[i] is not None and row[i] != 'm']

        # Check for zero variance
        if len(set(column)) == 1:
            # Skip columns with zero variance
            continue

        mean_val = sum(column) / len(column)

        # Check for zero standard deviation
        if len(column) > 1:
            std_dev = (sum((x - mean_val) ** 2 for x in column) / len(column)) ** 0.5
        else:
            std_dev = 0

        for row in matrix:
            if row[i] is not None and row[i] != 'm':
                # Check for NaN values
                if std_dev != 0:
                    row[i] = (float(row[i]) - mean_val) / std_dev
                else:
                    row[i] = 0  # Assigning a default value for zero standard deviation

    return matrix


def custom_random():
    seed = 1
    while True:
        seed = (seed * 1103515245 + 12345) & 0x7FFFFFFF
        yield seed / 0x7FFFFFFF


def svd_sklearn(data_matrix, num_components):
    imputer = SimpleImputer(strategy='mean')
    data_matrix_imputed = imputer.fit_transform(data_matrix)

    scaler = StandardScaler()
    data_matrix_standardized = scaler.fit_transform(data_matrix_imputed)

    svd = TruncatedSVD(n_components=num_components)
    svd_result = svd.fit_transform(data_matrix_standardized)

    return svd_result


def pca_sklearn_with_imputation(data_matrix, num_components):
    imputer = SimpleImputer(strategy='mean')
    data_matrix_imputed = imputer.fit_transform(data_matrix)

    scaler = StandardScaler()
    data_matrix_standardized = scaler.fit_transform(data_matrix_imputed)

    pca = PCA(n_components=num_components)
    pca_result = pca.fit_transform(data_matrix_standardized)

    return pca_result


def display_matrix(matrix):
    for row in matrix:
        print("|".join(f"{str(cell):^10}" for cell in row))


# locally loading and preprocessing data for each year
file_path_2017 = r'.\dataset\2017.arff' 
file_path_2018 = r'.\dataset\2018.arff'
file_path_2019 = r'.\dataset\2019.arff'
file_path_2020 = r'.\dataset\2020.arff'
file_path_2021 = r'.\dataset\2021 Q1.arff'

data_2017 = load_arff(file_path_2017)
data_2018 = load_arff(file_path_2018)
data_2019 = load_arff(file_path_2019)
data_2020 = load_arff(file_path_2020)
data_2021 = load_arff(file_path_2021)

data_2017_preprocessed = preprocess_data(data_2017)
data_2018_preprocessed = preprocess_data(data_2018)
data_2019_preprocessed = preprocess_data(data_2019)
data_2020_preprocessed = preprocess_data(data_2020)
data_2021_preprocessed = preprocess_data(data_2021)

data_2017_preprocessed = linear_interpolation(data_2017_preprocessed)
data_2018_preprocessed = linear_interpolation(data_2018_preprocessed)
data_2019_preprocessed = linear_interpolation(data_2019_preprocessed)
data_2020_preprocessed = linear_interpolation(data_2020_preprocessed)
data_2021_preprocessed = linear_interpolation(data_2021_preprocessed)


data_combined = data_2017_preprocessed + data_2018_preprocessed + data_2019_preprocessed + data_2020_preprocessed + data_2021_preprocessed
display_data_table(data_combined)


attributes = list(data_combined[0].keys())


matrix = []
for entry in data_combined:
    row = [entry[attr] for attr in attributes[2:]] 
    matrix.append(row)


standardized_data = z_score_standardization(matrix)

num_components = 2
pca_result_sklearn = pca_sklearn_with_imputation(standardized_data, num_components)


print("\nScikit-learn PCA Result:")
display_matrix(pca_result_sklearn)

svd_result_sklearn = svd_sklearn(standardized_data, num_components)

print("\nScikit-learn SVD Result:")
display_matrix(svd_result_sklearn)

Num|    Country     |         X1          |        X2         |         X3          |        X4        |         X5          |         X6          |         X7          |        X8         |         X9          |         X10          |         X11          |         X12          |         X13         |         X14         |       X15        |         X16          |         X17          |         X18          |         X19          |        X20        |         X21          |        X22        |         X23         |       X24        |         X25         |         X26         |        X27        |        X28        |        X29         |        X30        |        X31        |         X32         |       X33        |        X34         |         X35         |         X36          |        X37        |         X38         |         X39          |        X40        |        X41        |        X42         |        X43        |       X44        |         X45         |         X46         

#### Conclusion <br>
<p>The main differences between my method and sklearn are in how we handle data centering, reduce dimensions, deal with sparse matrices, and choose algorithms. Unlike sklearn, I don't center the data. My approach computes the full Singular Value Decomposition (SVD), while sklearn's SVD gives a simpler version. Sklearn is good with sparse matrices, but my method might not be as efficient with them. Lastly, I use the Gram-Schmidt process for orthogonalization, while sklearn uses a fast randomized SVD solver or ARPACK. In conclusion, my method is wrong because i dont know what it supposed to be</p>